1.  **Free Kaggle Notebook V4 for SwarmUI - 1 August 2024**
1. **Flux Models Added**
1.  **Please read instructions carefully**
1. **Select T4 x2 GPU - Faster and can utilize both GPUs at the same time**
1. **Most updated version with config of this notebook will be on >**
1. **https://www.patreon.com/posts/106650931**
1.  **Tutorial Video : https://youtu.be/XFUZof6Skkw**

In [ ]:
# Step 1
# To be able to use more models we will use temp folder 
# You can add remove more models here before running this cell
# This cell downloads SDXL base model so you don't need to download during initial install
# After SwarmUI started you have to change root folder to /kaggle/temp to be able to use more Kaggle disk space
!mkdir -p /kaggle/temp
%cd /kaggle/temp
!mkdir -p /kaggle/temp/Stable-Diffusion
%cd /kaggle/temp/Stable-Diffusion
!wget https://huggingface.co/stabilityai/stable-diffusion-xl-base-1.0/resolve/main/sd_xl_base_1.0_0.9vae.safetensors -O "SDXL 1.0 Base.safetensors"
!wget https://huggingface.co/SG161222/RealVisXL_V4.0/resolve/main/RealVisXL_V4.0.safetensors -O "RealVisXL V4.safetensors"
!wget https://civitai.com/api/download/models/292213?token=5577db242d28f46030f55164cdd2da5d -O "Hyper Realism V3.safetensors"
!wget https://huggingface.co/adamo1139/stable-diffusion-3-medium-ungated/resolve/main/sd3_medium.safetensors -O "SD3 Medium.safetensors"

In [ ]:
#Optional Step
#Newest FLUX models if you want to use them
#For this to work you need to change root folder as explained above don't forget that
#Flux works with CFG 1 only don't forget that to not get blurry images
#flux1-dev-fp8 better quality requires 20 or more steps
#flux1-schnell is distilled and requires 4 or more steps - takes around 120 seconds for 1 image 1024x1024
#You can reduce resolution to generate faster

!mkdir -p /kaggle/temp/unet
%cd /kaggle/temp/unet
!wget "https://huggingface.co/Kijai/flux-fp8/resolve/main/flux1-dev-fp8.safetensors" -O "flux1-dev-fp8.safetensors"
!wget "https://huggingface.co/black-forest-labs/FLUX.1-schnell/resolve/main/flux1-schnell.sft" -O "flux1-schnell.sft"
!mkdir -p /kaggle/temp/VAE
%cd /kaggle/temp/VAE
!wget "https://huggingface.co/black-forest-labs/FLUX.1-schnell/resolve/main/ae.sft" -O "ae.sft"

In [ ]:
# Step 2
!pip install flask
!pip install pyngrok

### First you need to register and get a token. 
### I used gmail register >
### https://dashboard.ngrok.com/get-started/your-authtoken
### Skipped authenticator not necessary
### [Click here](https://cdn-uploads.huggingface.co/production/uploads/6345bd89fe134dfd7a0dba40/eRmm7HjCcKhqsTNTJXy9E.png) to see how a token looks like you need to get

In [ ]:
#Step 3 - repeat this step whenever you launch / re-launch SwarmUI
## First put your ngrok token to the below and then run this code
## It will give a link like this at below : https://2fc5-34-134-226-xxx.ngrok-free.app
## Open it and then run web ui and once web ui started that link will start working
import os
import threading

from flask import Flask
from pyngrok import ngrok, conf

conf.get_default().auth_token = "replace_with_your_ngrok_token"

os.environ["FLASK_ENV"] = "development"

app = Flask(__name__)

public_url = ngrok.connect(7801).public_url
print(" * ngrok tunnel \"{}\" -> \"http://0.0.0.0:{}/\"".format(public_url, 7801))

app.config["BASE_URL"] = public_url

@app.route("/")
def index():
    return "Hello from Colab!"

threading.Thread(target=app.run, kwargs={"use_reloader": False}).start()


In [ ]:
# Step 4 - do not execute this cell twice only 1 time necessary
# Follow tutorial video to learn how to make it work
# After SwarmUI started you have to change root folder to /kaggle/temp to be able to use more Kaggle disk space
# After first time change root path you need to restart the app
# After run this cell, click visit site to start install and then it will auto start the SwarmUI
import os
SCRIPT_DIR = os.path.dirname(os.path.realpath("__file__"))
os.chdir(SCRIPT_DIR)
%cd /kaggle/working
#!rm -r SwarmUI
# Accidental run prevention
if os.path.isdir("SwarmUI"):
    print("SwarmUI already exists in this directory. Please remove it before installing.")
else:
    if os.path.isfile("SwarmUI.sln"):
        print("SwarmUI already exists in this directory. Please remove it before installing.")
    else:
        # Download swarm
        !git clone https://github.com/mcmonkeyprojects/SwarmUI
        %cd SwarmUI
        !mkdir -p dlbackend/comfy/ComfyUI/custom_nodes
        %cd dlbackend/comfy/ComfyUI/custom_nodes
        !git clone https://github.com/ltdrdata/ComfyUI-Manager
        %cd /kaggle/working/SwarmUI
        
        # install dotnet
        os.chdir("launchtools")
        !rm dotnet-install.sh

        # https://learn.microsoft.com/en-us/dotnet/core/install/linux-scripted-manual#scripted-install
        !wget https://dot.net/v1/dotnet-install.sh -O dotnet-install.sh
        !chmod +x dotnet-install.sh

        # Note: manual installers that want to avoid home dir, add to both of the below lines: --install-dir $SCRIPT_DIR/.dotnet
        !./dotnet-install.sh --channel 8.0 --runtime aspnetcore
        !./dotnet-install.sh --channel 8.0
        os.chdir("..")

        # Launch
        !./launch-linux.sh --launch_mode none --data_dir "/kaggle/temp" --host 0.0.0.0

In [ ]:
# Step 5 - To run the app again after cancelling run this command
# But before running it make sure to get a new link above and click visit site after started this cell
# So repeat Step 3 before running this cell
# After SwarmUI started you have to change root folder to /kaggle/temp to be able to use more Kaggle disk space
# Initial model loads can be slow since we use temp disk
%cd /kaggle/working/SwarmUI
!./launch-linux.sh --launch_mode none --host 0.0.0.0

In [ ]:
# Run this cell to generate a zip file of all generated outputs
# The generated zip file will be in the kaggle working directory
# After click 3 dots and download
%cd /kaggle/working/SwarmUI

# Remove existing zip file if it exists
!rm -f ../generated_images.zip

# Create a new zip file with only the outputs folder
!zip -r ../generated_images.zip Output

# Navigate back to the original working directory if needed
%cd /kaggle/working/SwarmUI
